In [1]:
# Notebook parameters. Values here are for development only and 
# will be overridden when running via snakemake and papermill.
cohort_id = "CD-NU_Gbadolite_gamb_2015_Q3"
# cohort_id = 'ML-2_Kati_colu_2014_Q3'
# cohort_id = 'CI-LG_Agneby-Tiassa_colu_2012'
cohorts_analysis = "20230223"
contigs = ['2RL', '3RL', 'X']
sample_sets = "3.0"
min_cohort_size = 20
max_cohort_size = 50
h12_calibration_contig = '3L'
use_gcs_cache = False
dask_scheduler = "threads"

In [2]:
# Parameters
min_cohort_size = 20
max_cohort_size = 50
sample_sets = ["3.0"]
contigs = ["2RL", "3RL", "X"]
cohorts_analysis = "20230223"
h12_calibration_contig = "3L"
h12_signal_detection_min_delta_aic = 1000
h12_signal_detection_min_stat_max = 0.1
h12_signal_detection_gflanks = [6]
use_gcs_cache = False
dask_scheduler = "single-threaded"
cohort_id = "BF-09_Houet_colu_2014_Q3"


In [3]:
from IPython.display import Markdown, HTML
import malariagen_data
import numpy as np
import pandas as pd
from pyprojroot import here
import yaml
import dask
dask.config.set(scheduler=dask_scheduler);
from textwrap import dedent

import geopandas as gpd
import bokeh.layouts as bklay
import bokeh.plotting as bkplt
import bokeh.models as bkmod
import plotly.express as px

from bokeh.io import output_notebook # enables plot interface in J notebook

# N.B., do not add the "remove-output" tag to this cell!!! If you do,
# the bokeh javascript libraries will not get loaded in the generated
# HTML page. The call to output_notebook() injects javascript in the
# cell output which triggers the bokeh javascript libraries to be loaded
# in the page.
output_notebook(hide_banner=True)

# Burkina Faso / Houet / coluzzii / 2014 / Q3

In [4]:
# Load cohorts to find sample query to select samples for this cohort.

df_cohorts = gpd.read_file(here() / "build" / "final_cohorts.geojson").set_index("cohort_id")
cohort = df_cohorts.loc[cohort_id]
cohort

cohort_size                                                          32
country                                                    Burkina Faso
admin1_iso                                                        BF-09
admin1_name                                               Hauts-Bassins
admin2_name                                                       Houet
taxon                                                          coluzzii
year                                                               2014
quarter                                                               3
cohort_label                Burkina Faso / Houet / coluzzii / 2014 / Q3
sample_query          cohort_admin2_quarter == 'BF-09_Houet_colu_201...
latitude                                                      11.233566
longitude                                                      -4.44517
h12_window_size                                                  1000.0
country_alpha2                                                  

In [5]:
# Initialise access to MalariaGEN data.

extra_params = dict()
if use_gcs_cache:
    extra_params["url"] = "simplecache::gs://vo_agam_release"
    extra_params["simplecache"] = dict(cache_storage=(here() / "gcs_cache").as_posix())

ag3 = malariagen_data.Ag3(
    # Pin the version of the cohorts analysis for reproducibility.
    cohorts_analysis=cohorts_analysis,
    results_cache=(here() / "malariagen_data_cache").as_posix(),
    **extra_params,
)
ag3

<MalariaGEN Ag3 API client>
Storage URL             : gs://vo_agam_release/
Data releases available : 3.0, 3.1, 3.2, 3.3, 3.4, 3.5, 3.6, 3.7, 3.8
Results cache           : /home/sanjaynagi/selection-atlas/malariagen_data_cache
Cohorts analysis        : 20230223
AIM analysis            : 20220528
Site filters analysis   : dt_20200416
Software version        : malariagen_data 7.13.0
Client location         : unknown
---
Please note that data are subject to terms of use,
for more information see https://www.malariagen.net/data
or contact data@malariagen.net. For API documentation see 
https://malariagen.github.io/vector-data/ag3/api.html

In [6]:
# Load sample metadata for this cohort.

df_samples = ag3.sample_metadata(sample_query=cohort['sample_query'])
df_samples

sample_id partner_sample_id  contributor       country  \
0   VBS25720-5561STDY9810323           BF13-64  Austin Burt  Burkina Faso   
1   VBS25722-5561STDY9810325           BF13-66  Austin Burt  Burkina Faso   
2   VBS25724-5561STDY9810327           BF13-68  Austin Burt  Burkina Faso   
3                   AB0326-C            BF18-1  Austin Burt  Burkina Faso   
4                   AB0327-C            BF18-3  Austin Burt  Burkina Faso   
5                   AB0328-C            BF18-4  Austin Burt  Burkina Faso   
6                   AB0329-C            BF18-5  Austin Burt  Burkina Faso   
7                   AB0330-C            BF18-6  Austin Burt  Burkina Faso   
8                   AB0331-C            BF18-9  Austin Burt  Burkina Faso   
9                   AB0332-C           BF18-10  Austin Burt  Burkina Faso   
10                  AB0334-C           BF18-12  Austin Burt  Burkina Faso   
11                  AB0337-C           BF22-15  Austin Burt  Burkina Faso   
12                  AB0338-C           BF18-13  Austin Burt  Burkina Faso   
13                  AB0339-C           BF18-14  Austin Burt  Burkina Faso   
14                  AB0340-C           BF18-15  Austin Burt  Burkina Faso   
15                  AB0341-C           BF18-16  Austin Burt  Burkina Faso   
16                  AB0348-C           BF22-50  Austin Burt  Burkina Faso   
17                  AB0396-C            BF14-8  Austin Burt  Burkina Faso   
18                  AB0397-C            BF14-9  Austin Burt  Burkina Faso   
19                  AB0398-C           BF14-10  Austin Burt  Burkina Faso   
20                  AB0399-C           BF14-11  Austin Burt  Burkina Faso   
21                  AB0400-C           BF14-12  Austin Burt  Burkina Faso   
22                  AB0403-C           BF14-16  Austin Burt  Burkina Faso   
23                  AB0404-C           BF14-18  Austin Burt  Burkina Faso   
24                  AB0409-C           BF14-21  Austin Burt  Burkina Faso   
25                  AB0410-C           BF20-54  Austin Burt  Burkina Faso   
26                  AB0411-C           BF20-56  Austin Burt  Burkina Faso   
27                  AB0413-C           BF20-59  Austin Burt  Burkina Faso   
28                  AB0503-C            BF13-1  Austin Burt  Burkina Faso   
29                  AB0505-C           BF13-13  Austin Burt  Burkina Faso   
30                  AB0508-C           BF13-38  Austin Burt  Burkina Faso   
31                  AB0509-C           BF24-55  Austin Burt  Burkina Faso   
32                  AB0510-C           BF24-56  Austin Burt  Burkina Faso   
33                  AB0523-C           BF24-26  Austin Burt  Burkina Faso   
34                  AB0408-C           BF14-20  Austin Burt  Burkina Faso   

          location  year  month  latitude  longitude sex_call  ...  \
0   Souroukoudinga  2014      7    11.238     -4.235        F  ...   
1   Souroukoudinga  2014      7    11.238     -4.235        F  ...   
2   Souroukoudinga  2014      7    11.238     -4.235        F  ...   
3     Bana Village  2014      7    11.233     -4.472        F  ...   
4     Bana Village  2014      7    11.233     -4.472        F  ...   
5     Bana Village  2014      7    11.233     -4.472        F  ...   
6     Bana Village  2014      7    11.233     -4.472        F  ...   
7     Bana Village  2014      7    11.233     -4.472        F  ...   
8     Bana Village  2014      7    11.233     -4.472        F  ...   
9     Bana Village  2014      7    11.233     -4.472        F  ...   
10    Bana Village  2014      7    11.233     -4.472        F  ...   
11    Bana Village  2014      7    11.233     -4.472        F  ...   
12    Bana Village  2014      7    11.233     -4.472        F  ...   
13    Bana Village  2014      7    11.233     -4.472        F  ...   
14    Bana Village  2014      7    11.233     -4.472        F  ...   
15    Bana Village  2014      7    11.233     -4.472        F  ...   
16    Bana Village  2014      7    11.233     -4.472    

In [7]:
# Determine collection dates.

df_collection_dates = (
    df_samples
    .groupby(["year", "month"])
    .size()
    .reset_index()
    .rename(columns={0: 'count'})
)
df_collection_dates

year  month  count
0  2014      7     35

In [8]:
# Determine first and last collection months.

min_month = df_collection_dates["month"].min()
max_month = df_collection_dates["month"].max()

if min_month < 0:
    start_month = end_month = None
else:
    start_month = pd.to_datetime(min_month, format="%m").month_name()
    end_month = pd.to_datetime(max_month, format="%m").month_name()
    
start_month, end_month

('July', 'July')

In [9]:
# Determine unique collection locations.

df_locations = df_samples[["location", "longitude", "latitude"]].drop_duplicates()
df_locations

location  longitude  latitude
0  Souroukoudinga     -4.235    11.238
3    Bana Village     -4.472    11.233

In [10]:
# Extract provenance information about the samples.

df_contributors = df_samples[["release", "sample_set", "contributor"]].drop_duplicates()
df_contributors["study"] = df_contributors.apply(
    lambda v: "Ag1000G" if v["sample_set"].startswith("AG1000G") else "TODO",
    axis="columns"
)
df_contributors["release"] = df_contributors["release"].apply(
    lambda v: f"Ag{v}"
)
df_contributors.rename(columns={
    "contributor": "Contributor",
    "study": "Study",
    "release": "Data release",
    "sample_set": "Sample set",
}, inplace=True)
df_contributors.set_index(["Contributor", "Study", "Data release"], inplace=True)
df_contributors

Sample set
Contributor Study   Data release                                  
Austin Burt TODO    Ag3.4         1191-VO-MULTI-OLOUGHLIN-VMF00106
            Ag1000G Ag3.0                             AG1000G-BF-B

In [11]:
# Build a paragraph with summary information about the samples in this cohort.

n_locations = len(df_locations)

summary_info = f"""This cohort comprises {cohort['cohort_size']:,} samples from the 
*{cohort['taxon']}* taxon, collected from {n_locations} locations within the administrative 
division of {cohort['admin2_name']}, {cohort['admin1_name']}, {cohort['country']}."""

if start_month and start_month == end_month:
    summary_info += f""" Collections were made in {start_month} {cohort['year']}."""
elif start_month:
    summary_info += f""" Collections were made between {start_month} and {end_month} in {cohort['year']}."""
else:
    summary_info += f""" Collections were made in {cohort['year']}."""
    
display(Markdown(summary_info))


This cohort comprises 32 samples from the 
*coluzzii* taxon, collected from 2 locations within the administrative 
division of Houet, Hauts-Bassins, Burkina Faso. Collections were made in July 2014.

## Selection scans

In [12]:
# load signals to overlay on H12 plots
import pandas as pd

df_signals_contigs = []
for contig in contigs:

    try:
        df_signals_contig = pd.read_csv(here() / "build/h12-signal-detection/" / f"{cohort_id}_{contig}.csv")
    except pd.errors.EmptyDataError:
        df_signals_contig = pd.DataFrame()
    df_signals_contigs.append(df_signals_contig)  
    
df_signals = pd.concat(df_signals_contigs)

# Add extra columns to help with overlaying signals on plots.
df_signals["bottom"] = 0
df_signals["top"] = 1

df_signals

cohort_id contig     gcenter   pcenter  delta_i  stat_max  \
0  BF-09_Houet_colu_2014_Q3    2RL   49.729818  24864910     1852  0.205078   
1  BF-09_Houet_colu_2014_Q3    2RL   56.983658  28491829     5845  0.273438   
2  BF-09_Houet_colu_2014_Q3    2RL   81.895459  40947730     3401  0.166016   
3  BF-09_Houet_colu_2014_Q3    2RL  120.988207  64264735     3628  1.000000   
4  BF-09_Houet_colu_2014_Q3    2RL  166.499016  87020140     5735  0.326660   
0  BF-09_Houet_colu_2014_Q3    3RL   57.058801  28529401     5590  0.291016   
0  BF-09_Houet_colu_2014_Q3      X   18.486110   9243055     1237  0.105469   
1  BF-09_Houet_colu_2014_Q3      X   30.245270  15122636     6458  1.000000   

     gpos_max  ppos_max  focus_gstart  focus_gstop  ...      skew  decay_left  \
0   49.729818  24864909     49.672682    49.758387  ...  0.499974    0.228544   
1   56.920910  28460455     56.846269    57.124450  ... -0.017650    0.549556   
2   81.845514  40922757     81.838021    81.940728  ...  0.171738    0.229751   
3  120.690942  64116102    120.717300   121.123661  ...  0.500000    1.083629   
4  166.466226  87003744    166.324842   166.586103  ...  0.500000    0.696696   
0   57.200368  28600184     56.985785    57.146897  ... -0.135431    0.292063   
0   18.515120   9257560     18.456725    18.507379  ...  0.233164    0.117541   
1   30.392838  15196419     30.125288    30.446328  ... -0.372399    0.479927   

   decay_right  baseline           aic           bic        rss  constant_aic  \
0     0.114276  0.028752 -18691.391462 -18663.142999   0.284867 -16839.062436   
1     0.563168  0.029021 -18389.061289 -18360.921133   0.265728 -12543.265643   
2     0.181076  0.024346 -16513.000595 -16486.071340   0.057395 -13111.226423   
3     0.541815  0.018370  -7634.394845  -7607.739543  10.225737  -4005.491436   
4     0.348348  0.019825 -17603.703279 -17575.804885   0.242662 -11867.794038   
0     0.352383  0.019536 -17071.058072 -17043.416413   0.191086 -11480.120863   
0     0.085077  0.024325 -19105.375487 -19077.653826   0.076564 -17868.149302   
1     0.804233  0.039246 -12225.248176 -12197.437367   3.329709  -5766.728197   

   bottom  top  
0       0    1  
1       0    1  
2       0    1  
3       0    1  
4       0    1  
0       0    1  
0       0    1  
1       0    1  

[8 rows x 32 columns]

In [13]:
# load window sizes 
h12_calibration_dir = "build/h12-calibration"
with open(here() / h12_calibration_dir / f"{cohort_id}.yaml") as h12_calibration_file:
    h12_calibration_params = yaml.safe_load(h12_calibration_file)
h12_window_size = h12_calibration_params["h12_window_size"]
g123_calibration_dir = "build/g123-calibration"
with open(here() / g123_calibration_dir / f"{cohort_id}.yaml") as g123_calibration_file:
    g123_calibration_params = yaml.safe_load(g123_calibration_file)
g123_window_size = g123_calibration_params["g123_window_size"]

if cohort.taxon == 'arabiensis':
    phasing_analysis = 'arab'
else:
    phasing_analysis = 'gamb_colu'

ihs_window_size = 100

def plot_h12_g123_ihs_tracks(
        contig, 
        df_signals,
        sizing_mode='stretch_width', 
        show=False, 
        width=800, 
        track_height=150,
        genes_height=90,
    ):

    sample_query = cohort["sample_query"]
    
    fig1 = ag3.plot_h12_gwss_track(
        contig=contig, 
        window_size=h12_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        show=show,
        width=width,
        height=track_height,
    )
    fig1.xaxis.visible = False
        
    if not df_signals.empty:
        df = df_signals.query("contig == @contig")
        center_xs = [np.array([row.pcenter, row.pcenter]) for idx, row in df.iterrows()]
        center_ys = [np.array([0, 1]) for idx, row in df.iterrows()]
        source = bkmod.ColumnDataSource(data={
            'cohort': df.cohort_id,
            'chromosome': df.contig,
            'score': df.delta_i.astype(int),
            'peak_start': df.span2_pstart,
            'peak_stop': df.span2_pstop,
            'focus_start': df.focus_pstart,
            'focus_stop': df.focus_pstop,    
            'center_xs': center_xs,
            'center_ys': center_ys,
            'bottom': df.bottom ,
            'top': df.top,
            })
        quad = fig1.quad(bottom='bottom', top='top', left='peak_start', right='peak_stop', 
              source=source, color="gray", alpha=.1, line_width=1)
        quad2 = fig1.quad(bottom='bottom', top='top', left='focus_start', right='focus_stop', 
              source=source, color="red", alpha=.4)
        glyph = bkmod.MultiLine(xs='center_xs', ys='center_ys', line_color='red', line_width=2, line_alpha=0.8)
        fig1.add_glyph(source, glyph)
    
        hover = bkmod.HoverTool(tooltips=[
            ("Cohort", '@cohort'),
            ("Score", '@score'),
            ("Focus", "@focus_start{,} - @focus_stop{,}"),
        ], renderers=[quad])

        fig1.add_tools(hover)
    
    fig2 = ag3.plot_g123_gwss_track(
        contig=contig, 
        window_size=g123_window_size, 
        sites=phasing_analysis,
        site_mask=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig2.xaxis.visible = False

    fig3 = ag3.plot_ihs_gwss_track(
        contig=contig, 
        window_size=ihs_window_size, 
        analysis=phasing_analysis, 
        sample_sets=sample_sets,
        sample_query=sample_query, 
        min_cohort_size=min_cohort_size,
        max_cohort_size=max_cohort_size,
        sizing_mode=sizing_mode,
        width=width,
        height=track_height,
        show=show,
        title="",
        x_range=fig1.x_range,
    )
    fig3.xaxis.visible = False


    fig4 = ag3.plot_genes(
        region=contig, 
        show=show,
        sizing_mode=sizing_mode,
        width=width,
        height=genes_height,
        x_range=fig1.x_range
        )
                        
    fig = bklay.gridplot(
        [fig1, fig2, fig3, fig4],
        ncols=1,
        toolbar_location="above",
        merge_tools=True,
        sizing_mode=sizing_mode,
    )
    return fig 

In [14]:
for contig in contigs:
    
    display(HTML(f"<h3>Chromosome {contig}</h3>"))
    
    fig = plot_h12_g123_ihs_tracks(
        contig=contig,
        df_signals=df_signals,
    );

    bkplt.show(fig)


## Sampling information

In [15]:
from ipyleaflet import Map, Marker, basemaps
from ipywidgets import HTML

center = cohort[['latitude', 'longitude']].to_list()
m = Map(center=center, zoom=9, basemap=basemaps.OpenTopoMap)

df = df_samples[['latitude', 'longitude', 'taxon']].groupby(['latitude', 'longitude', 'taxon']).size().to_frame().rename(columns={0: 'count'}).reset_index()

for coh_id, row in df.iterrows():
    lat, long = row[['latitude', 'longitude']]
    
    if row['taxon'] == 'gambiae':
        color= 'red'
    elif row['taxon'] == 'coluzzii':
        color='cadetblue'
    elif row['taxon'] == 'arabiensis':
        color='lightgreen'
    else: 
        color='gray'

    marker = Marker(location=(lat, long), draggable=False, opacity=0.7, color=color)
    m.add_layer(marker);

    message2 = HTML()
    message2.value = f"n = {row['count']}"
    marker.popup = message2

display(m)

Map(center=[11.233566037735851, -4.445169811320756], controls=(ZoomControl(options=['position', 'zoom_in_text'…

In [16]:

if min_month >= 0:
    # For this cohort we have month data, so show a breakdown of sample
    # numbers by location and month.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.pivot_table(
        index=["location", "longitude", "latitude"],
        columns="month",
        values="sample_id",
        aggfunc="count",
        fill_value=0,
    )

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude")] + 
        [("Date", pd.to_datetime(x, format="%m").month_name()) 
         for x in df_loc_dt.columns[3:]], 
    )
    df_loc_dt.columns = cols
    
else:
    # For this cohort we do not have month data, so show a breakdown of sample
    # numbers by location only.
    
    # Construct a pivot table counting samples.
    df_loc_dt = df_samples.groupby(["location", "longitude", "latitude"]).agg({"sample_id": "count"})

    # Tidy up the columns using a multi index.
    df_loc_dt.reset_index(inplace=True)
    cols = pd.MultiIndex.from_tuples(
        [("Location", "Name"), ("Location", "Longitude"), ("Location", "Latitude"), ("Date", cohort.year)]
    )
    df_loc_dt.columns = cols

# Style the table.
df_loc_dt_styled = (
    df_loc_dt
    .style
    .format(precision=3)
    .set_caption("Number of samples collected.")
    .hide()
)
display(df_loc_dt_styled)    

## Diagnostics
### H12 calibration

In [17]:
display(Markdown(f"Selected window size: **{h12_window_size:,}**"))

window_sizes = (100, 200, 500, 1000, 2000, 5000, 10000, 20000)

ag3.plot_h12_calibration(
    contig=h12_calibration_contig,
    analysis=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);


Selected window size: **1,000**

### G123 Calibration

In [18]:
display(Markdown(f"Selected window size: **{g123_window_size:,}**"))

ag3.plot_g123_calibration(
    contig=h12_calibration_contig,
    sites=phasing_analysis,
    site_mask=phasing_analysis,
    sample_sets=sample_sets,
    sample_query=cohort['sample_query'],
    min_cohort_size=min_cohort_size,
    max_cohort_size=max_cohort_size,
    window_sizes=window_sizes,
);

Selected window size: **500**

## Data sources

In [19]:
df_sources_style = (
    df_contributors
    .style
    .set_caption("MalariaGEN Vector Observatory partners, studies and sample sets contributing data for this cohort.")
)
df_sources_style